# How to develop a MEC application using the MEC Sandbox HTTP REST API

## Table of contents

1. What is a MEC applicationn](what_is_a_mec_applicationn)
2. The basics of developing a MEC applicationh](the_basics_of_developing_a_mec_application)
3. [Use the MEC Sandbox HTTP REST API models and code](#use_the_mec_sandbox_http_rest_api_models_and_code)
4. [Create our first MEC application](#create_our_first_mec_application)
    4.1. [The login function](#the_login_function)
    4.2. [The logout function](#the_logout_function)
5. [Second step: Retrieve the list of network scenarios](#second_step_retrieve_the_list_of_network_scenarios)
6. [Third step: Activate and deactivate a network scenario](#third_step_activate_and_deactivate_a_network_scenario)
    6.1. [The activate function](#the_activate_function)
    6.2. [The deactivate function](#thedeactivate_function)
7. [Fourth step: Create and delete an appliction instance id](#fourth_step_create_and_delete_an_appliction_instance_id)
8. [MEC Registration and the READY indication](#mec_registration_and_the_ready_indication)
9. [Annexes](#annexes)
10. [Bibliography](#bibliography)t


## What is a MEC application

See [The Wiki MEC web site](https://www.etsi.org/technologies/multi-access-edge-computing)


## The basics of developing a MEC application

The developement of a MEC application follows a strict process in order to access the ETSI MEC services and provides valueable services to the customers.
Mainly, this process can be split in several steps:
1. Global initializations (constant, variables...)
2. Create of a new instance of a MEC Sandbox (Note that using an existing one could be a solution too (see Annex A)
3. Activate a network scenario in order to access the ETSI MEC services
4. Create a new application identifier
5. Register our MEC application and subscribe to service termination (see MEC 011)
6. Use MEC services in order to provide valueable services to the customers
    6.1. Apply MEC services required subscriptions (e.g. MEC 013 location subscription)
7. Terminate the MEC application
    7.1. Remove MEC services subscriptions
    7.2. Deactivate the current network scenario
    7.3. Delete the instance of the MEC Sandbox
8. Release all the MEC application resources

## Use the MEC Sandbox HTTP REST API models and code

The MEC sandbox provides a piece of code (the python sub) that shall be used to develop the MEC applicationand interact with the MEC Sandbox. This piece of code mainly contains swagger models to serialize/deserialize JSON data structures and HTTP REST API call functions.
The openApi file is availabe [here](https://forge.etsi.org/rep/mec/AdvantEDGE/-/blob/Task2_PoC/go-apps/meep-sandbox-api/api/swagger.yaml) and the [Swagger editor](https://editor-next.swagger.io/) is used to generate the python sub.

The project architecture is describe below:

```sh
.
├── mecapp
│   ├── docs
│   ├── swagger_client
│   │   ├── api
│   │   │   └── __pycache__
│   │   ├── models
│   │   │   └── __pycache__
│   │   └── __pycache__
│   └── notebook
 te└
 ebirectory:

The api folder contains the python implementation of the HTTP REST API definitions introduced by the openApi [file](https://forge.etsi.org/rep/mec/AdvantEDGE/-/blob/Task2_PoC/go-apps/meep-sandbox-api/api/swagger.yaml).
The model folder contains the python implementation of the data type definitions introduced by the openApi [file](https://forge.etsi.org/rep/mec/AdvantEDGE/-/blob/Task2_PoC/go-apps/meep-sandbox-api/api/swagger.yaml).

Before to create our MEC ap[plication skeleton, the following steps shall be done:
1) Change the working directory (see the project architecture)

In [ ]:
import os
os.chdir(os.path.join(os.getcwd(), '../mecapp'))
print(os.getcwd())

2) Do the python import

In [ ]:
from __future__ import division # Import floating-point division (1/4=0.25) instead of Euclidian division (1/4=0)

import os
import sys
import logging
import time
import json
import uuid

from pprint import pprint

import swagger_client
from swagger_client.rest import ApiException


3) to initialize the global constants (cell 3)

In [ ]:
MEC_SANDBOX     = 'https://mec-platform.etsi.org/sandbox-api/v1'         # MEC Sandbox host/base URL
PROVIDER        = 'gitlab'                                               # Login provider value
MEC_PLTF        = 'mep1'                                                 # MEC plateform name. Linked to the network scenario
LOGGER_FORMAT   = '%(asctime)s - %(name)s - %(levelname)s - %(message)s' # Logging format
STABLE_TIME_OUT = 6

4) to setup a logger instance and initialize the global variables  (cell 4)

In [ ]:
# Initialize the logger
logger = logging.getLogger(__name__)
logger.setLevel(logging.DEBUG)
logging.basicConfig(filename='/tmp/' + time.strftime("%Y%m%d-%H%M%S") + '.log')
l = logging.StreamHandler()
l.setFormatter(logging.Formatter('%(asctime)s - %(name)s - %(levelname)s - %(message)s'))
logger.addHandler(l)

# Setup the HTTP REST API configuration
configuration               = swagger_client.Configuration()
configuration.host          = MEC_SANDBOX
configuration.verify_ssl    = False
configuration.debug         = True
configuration.logger_format = LOGGER_FORMAT

# Initialize the global variables
nw_scenarios    = []   # The list of available network scenarios
nw_scenario_idx = -1   # The network scenario idx to activate (deactivate)
app_inst_id     = None # The requested application instance identifier


## Create our first MEC application

The first step to develop a MEC application is to create the application skeleton which contains the minimum steps below:
 
- Login to instanciate a MEC Sandbox
- Logout to delete a existing MEC Sandbox

### First steps: the login/logout

Here is the first squeleton with the following sequence:
- Login
- Print sandbox identifier
- Logout
- Check that logout is effective


#### The login function

It uses the HTTP POST request with the URL 'POST /sandbox-api/v1/login?provide=gitlab' (see PROVIDER constant).


In [ ]:
# Login
def process_login() -> swagger_client.Sandbox:
    """
    Authenticate and create a new MEC Sandbox instance.

    :return: The swagger_client.Sandbox instance on success, None otherwise
    """ 

    global PROVIDER, MEC_SANDBOX, LOGGER_FORMAT, logger, configuration

    logger.debug(">>> process_login")

    try:
        api = swagger_client.ApiClient(configuration, 'Content-Type', 'application/json')
        auth = swagger_client.AuthorizationApi(api)
        result = auth.login(PROVIDER, async_req = False)  # noqa: E501
        logger.debug("process_login: result: " + str(result))
        return result
    except ApiException as e:
        logger.error("Exception when calling AuthorizationApi->login: %s\n" % e)

    return None
    # End of function process_login


#### The logout function

It uses the HTTP POST request with the URL 'POST /sandbox-api/v1/logout?sandbox_name={sandbox_name}'.


In [ ]:
# Logout
def process_logout(sandbox: swagger_client.Sandbox) -> int:
    """
    Delete the specified MEC Sandbox instance.

    :param sandbox: The MEC Sandbox to delete
    :return: 0 on success, -1 otherwise
    """

    global PROVIDER, MEC_SANDBOX, LOGGER_FORMAT, logger, configuration

    logger.debug(">>> process_logout: sandbox.name=" + sandbox.name)

    try:
        api = swagger_client.ApiClient(configuration, 'Content-Type', 'application/json')
        auth = swagger_client.AuthorizationApi(api)
        result = auth.logout(sandbox.name, async_req = False)  # noqa: E501
        return 0
    except ApiException as e:
        logger.error("Exception when calling AuthorizationApi->logout: %s\n" % e)
    return -1
    # End of function process_logout


Now, let put in action our Login/Logout functions:

In [ ]:
def process_main():
    """
    This is the skeleton of our MEC application:
        - Login
        - Print sandbox identifier
        - Logout
        - Check that logout is effective
    This skeleton will be the bas of the next sprint in order to achieve a full implementation of a MEC application
    """ 

    global PROVIDER, MEC_SANDBOX, LOGGER_FORMAT, logger

    logger.debug("Starting at " + time.strftime("%Y%m%d-%H%M%S"))
    logger.debug("\t pwd= " + os.getcwd())

    # Login
    sandbox = process_login()
    if sandbox is None:
        return

    # Print sandbox identifier
    logger.info("Sandbox created: " + sandbox.name)
    # Wait for the MEC Sandbox is running
    time.sleep(STABLE_TIME_OUT) # Sleep for 3 seconds

    # Logout
    process_logout(sandbox)

    # Check that logout is effective
    logger.debug("To check that logout is effective, verify on the MEC Sandbox server that the MEC Sandbox is removed (kubectl get pods -A")
  
    logger.debug("Stopped at " + time.strftime("%Y%m%d-%H%M%S"))
    # End of function process_main

if __name__ == '__main__':
    process_main()


### Second step: Retrieve the list of network scenarios

Let's go futhur and see how we can retrieve the list of the network scenarios available in order to activate one of them and access the MEC services exposed such as MEC 013 or MEC 030.

The sequence will be:
- Login
- Print sandbox identifier
- Print available network scenarios
- Logout
- Check that logout is effective

The login and logout functions are described in cell 3 and 4.

To retrieve the list of the network scenarios, let's create a new function called 'get_network_scenarios'. It uses the HTTP GET request with the URL '/sandbox-api/v1/sandboxNetworkScenarios?sandbox_name={sandbox_name}'.

In [ ]:
def get_network_scenarios(sandbox: swagger_client.Sandbox) -> list:
    """
    Retrieve the list of the available network scenarios.

    :param sandbox: The MEC Sandbox instance to use
    :return: The list of the available network scenarios on success, None otherwise
    """

    global PROVIDER, MEC_SANDBOX, LOGGER_FORMAT, logger, configuration

    logger.debug(">>> get_network_scenarios: sandbox.name=" + sandbox.name)

    try:
        api = swagger_client.ApiClient(configuration, 'Content-Type', 'application/json')
        nw = swagger_client.SandboxNetworkScenariosApi(api)
        result = nw.sandbox_network_scenarios_get(sandbox.name, async_req = False)  # noqa: E501
        logger.debug("get_network_scenarios: result: " + str(result))
        return result
    except ApiException as e:
        logger.error("Exception when calling SandboxNetworkScenariosApi->sandbox_network_scenarios_get: %s\n" % e)

    return None
    # End of function get_network_scenarios


Putting everything together:

In [ ]:
def process_main():
    """
    This is the first sprint of our skeleton of our MEC application:
        - Login
        - Print sandbox identifier
        - Print available network scenarios
        - Logout
        - Check that logout is effective
    """ 
    global PROVIDER, MEC_SANDBOX, LOGGER_FORMAT, nw_scenarios, logger

    logger.debug("Starting at " + time.strftime("%Y%m%d-%H%M%S"))
    logger.debug("\t pwd= " + os.getcwd())

    # Login
    sandbox = process_login()
    if sandbox is None:
        logger.error("Failed to instanciate a MEC Sandbox")
        return

    # Print sandbox identifier
    logger.info("Sandbox created: " + sandbox.name)
    # Wait for the MEC Sandbox is running
    time.sleep(STABLE_TIME_OUT) # Sleep for 3 seconds

    # Print available network scenarios
    nw_scenarios = get_network_scenarios(sandbox)
    if nw_scenarios is None:
        logger.error("Failed to retrieve the list of network scenarios")
    elif len(nw_scenarios) != 0:
        logger.info("nw_scenarios: %s", str(type(nw_scenarios[0])))
        logger.info("nw_scenarios: %s", str(nw_scenarios))
    else:
        logger.info("nw_scenarios: No scenario available")

    # Logout
    process_logout(sandbox)

    # Check that logout is effective
    logger.debug("To check that logout is effective, verify on the MEC Sandbox server that the MEC Sandbox is removed (kubectl get pods -A")
  
    logger.debug("Stopped at " + time.strftime("%Y%m%d-%H%M%S"))
    # End of function process_main

if __name__ == '__main__':
    process_main()


### Third step: Activate and deactivate a network scenario

Having a list of network scenarion, the next step is to actvate (and deactivate) a network scenario. This step is mandatory to create a new application instance id and access the MEC services.

In this section, we will arbitrary activate the network scenario called '4g-5g-macro-v2x', which is at the index 0 of the nw_scenarios. 

In [ ]:
def select_network_scenario_based_on_criteria(criterias_list: list) -> int:
    """
    Select the network scenario to activate based of the provided list of criterias.

    :param criterias_list: The list of criterias to select the correct network scenario
    :return: 0 on success, -1 otherwise
    """
    return 0 # The index of the '4g-5g-macro-v2x' network scenario - Hard coded

#### The activate function

The process to activate a scenario is based on an HTTP POST request with the URL '/sandboxNetworkScenarios/{sandbox_name}?network_scenario_id={network_scenario_id}'.


In [ ]:
def activate_network_scenario(sandbox: swagger_client.Sandbox) -> int:
    """
    Activate the specified network scenario.

    :param sandbox: The MEC Sandbox instance to use
    :return: 0 on success, -1 otherwise
    """

    global MEC_SANDBOX, LOGGER_FORMAT, logger, configuration, nw_scenarios, nw_scenario_idx

    logger.debug(">>> activate_network_scenario: " + sandbox.name)

    nw_scenario_idx = select_network_scenario_based_on_criteria([])
    if nw_scenario_idx == -1:
        logger.error("activate_network_scenario: Failed to select a network scenarion")
        return -1

    try:
        api = swagger_client.ApiClient(configuration, 'Content-Type', 'application/json')
        nw = swagger_client.SandboxNetworkScenariosApi(api)
        result = nw.sandbox_network_scenario_post(sandbox.name, nw_scenarios[nw_scenario_idx].id, async_req = False)  # noqa: E501
        logger.debug("activate_network_scenario: result: " + str(result))
        return result
    except ApiException as e:
        logger.error("Exception when calling SandboxNetworkScenariosApi->activate_network_scenario: %s\n" % e)

    return -1
    # End of function activate_network_scenario


#### The deactivate function

The process to deactivate a scenario is based on an HTTP DELETE request with the URL '/sandboxNetworkScenarios/{sandbox_name}?network_scenario_id={network_scenario_id}'.


In [ ]:
def deactivate_network_scenario(sandbox: swagger_client.Sandbox) -> int:
    """
    Deactivate the current network scenario.

    :param sandbox: The MEC Sandbox instance to use
    :return: 0 on success, -1 otherwise
    """

    global MEC_SANDBOX, LOGGER_FORMAT, logger, configuration, nw_scenarios, nw_scenario_idx

    logger.debug(">>> deactivate_network_scenario: " + sandbox.name)

    try:
        api = swagger_client.ApiClient(configuration, 'Content-Type', 'application/json')
        nw = swagger_client.SandboxNetworkScenariosApi(api)
        result = nw.sandbox_network_scenario_delete(sandbox.name, nw_scenarios[nw_scenario_idx].id, async_req = False)  # noqa: E501
        logger.debug("deactivate_network_scenario: result: " + str(result))
        return result
    except ApiException as e:
        logger.error("Exception when calling SandboxNetworkScenariosApi->deactivate_network_scenario: %s\n" % e)

    return -1
    # End of function deactivate_network_scenario


Now, it is time to create the second iteration of our MEC application.

The sequence is the following:
- Login
- Print sandbox identifier
- Print available network scenarios
- Activate a network scenario
- Check that the network scenario is activated and the MEC services are running
- Deactivate a network scenario
- Logout
- Check that logout is effective



In [ ]:
def process_main():
    """
    This is the second sprint of our skeleton of our MEC application:
        - Login
        - Print sandbox identifier
        - Print available network scenarios
        - Activate a network scenario
        - Check that the network scenario is activated and the MEC services are running
        - Deactivate a network scenario
        - Logout
        - Check that logout is effective
    """ 
    global PROVIDER, MEC_SANDBOX, LOGGER_FORMAT, nw_scenarios, logger

    logger.debug("Starting at " + time.strftime("%Y%m%d-%H%M%S"))
    logger.debug("\t pwd= " + os.getcwd())

    # Login
    sandbox = process_login()
    if sandbox is None:
        logger.error("Failed to instanciate a MEC Sandbox")
        return

    # Print sandbox identifier
    logger.info("Sandbox created: " + sandbox.name)
    # Wait for the MEC Sandbox is running
    time.sleep(STABLE_TIME_OUT) # Sleep for 3 seconds

    # Print available network scenarios
    nw_scenarios = get_network_scenarios(sandbox)
    if nw_scenarios is None:
        logger.error("Failed to retrieve the list of network scenarios")
    elif len(nw_scenarios) != 0:
        logger.info("nw_scenarios: %s", str(type(nw_scenarios[0])))
        logger.info("nw_scenarios: %s", str(nw_scenarios))
        # Wait for the MEC Sandbox is running
        time.sleep(STABLE_TIME_OUT) # Sleep for 3 seconds
    else:
        logger.info("nw_scenarios: No scenario available")

    # Activate a network scenario based on a list of criterias (hard coded!!!)
    if activate_network_scenario(sandbox) == -1:
        logger.error("Failed to activate network scenario")
    else:
        logger.info("Network scenario activated: " + nw_scenarios[nw_scenario_idx].id)
        # Wait for the MEC services are running
        time.sleep(STABLE_TIME_OUT) # Sleep for 3 seconds

    # Check that the network scenario is activated and the MEC services are running 
    logger.info("To check that the network scenario is activated, verify on the MEC Sandbox server that the MEC services are running (kubectl get pods -A")
    time.sleep(60) # Sleep for 3 seconds

    # Deactivate a network scenario based on a list of criterias (hard coded!!!)
    if deactivate_network_scenario(sandbox) == -1:
        logger.error("Failed to deactivate network scenario")
    else:
        logger.info("Network scenario deactivated: " + nw_scenarios[nw_scenario_idx].id)
        # Wait for the MEC services are terminated
        time.sleep(STABLE_TIME_OUT)

    # Logout
    process_logout(sandbox)

    # Check that logout is effective
    logger.debug("To check that logout is effective, verify on the MEC Sandbox server that the MEC Sandbox is removed (kubectl get pods -A")
  
    logger.debug("Stopped at " + time.strftime("%Y%m%d-%H%M%S"))
    # End of function process_main

if __name__ == '__main__':
    process_main()


### Fourth step: Create and delete an appliction instance id

To enable our MEC application to be part of the activated network scenario, we need to request the MEC sandbox to create a new application instance identifer. Our MEC application will use this identifier to register to the MEC Sandbox according to MEC 011.

#### The appliction instance id creation function



In [ ]:
def request_application_instance_id(sandbox: swagger_client.Sandbox) -> swagger_client.models.ApplicationInfo:
    """
    """

    global MEC_SANDBOX, LOGGER_FORMAT, logger, configuration, app_inst_id

    logger.debug(">>> request_application_instance_id: " + sandbox.name)

    # Create a instance of our MEC application
    a = swagger_client.models.ApplicationInfo(id=uuid.uuid4(), name='JupyterMecApp', node_name=MEC_PLTF, type='USER'):  # noqa: E501
    
    try:
        api = swagger_client.ApiClient(configuration, 'Content-Type', 'application/json')
        nw = swagger_client.SandboxAppInstancesApi(api)
        result = nw.sandbox_app_instances_post(sandbox.name, a, async_req = False)  # noqa: E501
        logger.debug("request_application_instance_id: result: " + str(result))
        return result
    except ApiException as e:
        logger.error("Exception when calling SandboxAppInstancesApi->sandbox_app_instances_post: %s\n" % e)

    return None
    # End of function request_application_instance_id

#### The appliction instance id deletion function



In [ ]:
def deletet_application_instance_id(sandbox: swagger_client.Sandbox) -> int:
    """
    """

    global MEC_SANDBOX, LOGGER_FORMAT, logger, configuration, app_inst_id

    logger.debug(">>> deletet_application_instance_id: " + sandbox.name)

    try:
        api = swagger_client.ApiClient(configuration, 'Content-Type', 'application/json')
        nw = swagger_client.SandboxAppInstancesApi(api)
        result = nw.sandbox_app_instances_delete(sandbox.name, app_inst_id.id, async_req = False)  # noqa: E501
        logger.debug("deletet_application_instance_id: result: " + str(result))
        return result
    except ApiException as e:
        logger.error("Exception when calling SandboxAppInstancesApi->sandbox_app_instances_delete: %s\n" % e)

    return -1
    # End of function deletet_application_instance_id

It is time now to create the our third iteration of our MEC application.

The sequence is the following:
- Login
- Print sandbox identifier
- Print available network scenarios
- Activate a network scenario
- Request for a new application instance identifer
- Check 
- Delete our application instance identifer
- Deactivate a network scenario
- Logout
- Check that logout is effective


In [ ]:
def process_main():
    """
    This is the second sprint of our skeleton of our MEC application:
        - Login
        - Print sandbox identifier
        - Print available network scenarios
        - Activate a network scenario
        - Check that the network scenario is activated and the MEC services are running
        - Deactivate a network scenario
        - Logout
        - Check that logout is effective
    """ 
    global PROVIDER, MEC_SANDBOX, LOGGER_FORMAT, nw_scenarios, logger

    logger.debug("Starting at " + time.strftime("%Y%m%d-%H%M%S"))
    logger.debug("\t pwd= " + os.getcwd())

    # Login
    sandbox = process_login()
    if sandbox is None:
        logger.error("Failed to instanciate a MEC Sandbox")
        return

    # Print sandbox identifier
    logger.info("Sandbox created: " + sandbox.name)
    # Wait for the MEC Sandbox is running
    time.sleep(STABLE_TIME_OUT) # Sleep for 3 seconds

    # Print available network scenarios
    nw_scenarios = get_network_scenarios(sandbox)
    if nw_scenarios is None:
        logger.error("Failed to retrieve the list of network scenarios")
    elif len(nw_scenarios) != 0:
        logger.info("nw_scenarios: %s", str(type(nw_scenarios[0])))
        logger.info("nw_scenarios: %s", str(nw_scenarios))
        # Wait for the MEC Sandbox is running
        time.sleep(STABLE_TIME_OUT) # Sleep for 3 seconds
    else:
        logger.info("nw_scenarios: No scenario available")

    # Activate a network scenario based on a list of criterias (hard coded!!!)
    if activate_network_scenario(sandbox) == -1:
        logger.error("Failed to activate network scenario")
    else:
        logger.info("Network scenario activated: " + nw_scenarios[nw_scenario_idx].id)
        # Wait for the MEC services are running
        time.sleep(STABLE_TIME_OUT) # Sleep for 3 seconds

    # Request for a new application instance identifer
    app_inst_id = request_application_instance_id(sandbox)
    if app_inst_id == None:
        logger.error("Failed to request an application instance identifer")
    else:
        logger.info("app_inst_id: %s", str(type(app_inst_id)))
        logger.info("app_inst_id: %s", str(app_inst_id))

    # Check that the network scenario is activated and the MEC services are running 
    logger.info("To check that the app_inst_id is created, verify on the MEC Sandbox server that the MEC services are running (kubectl get pods -A")
    time.sleep(3) # Sleep for 3 seconds

    # Request for a new application instance identifer
    if delete_application_instance_id(sandbox) == -1:
        logger.error("Failed to delete the application instance identifer")
    else:
        logger.info("app_inst_id deleted: " + app_inst_id.id)

    # Deactivate a network scenario based on a list of criterias (hard coded!!!)
    if deactivate_network_scenario(sandbox) == -1:
        logger.error("Failed to deactivate network scenario")
    else:
        logger.info("Network scenario deactivated: " + nw_scenarios[nw_scenario_idx].id)
        # Wait for the MEC services are terminated
        time.sleep(STABLE_TIME_OUT)

    # Logout
    process_logout(sandbox)

    # Check that logout is effective
    logger.debug("To check that logout is effective, verify on the MEC Sandbox server that the MEC Sandbox is removed (kubectl get pods -A")
  
    logger.debug("Stopped at " + time.strftime("%Y%m%d-%H%M%S"))
    # End of function process_main

if __name__ == '__main__':
    process_main()


## MEC Registration and the READY indication



# Annexes

## Annex A: How to use an existing MEC sandbox instance

TODO



# Bibliography

1. ETSI GS MEC 002 (V2.2.1) (01-2022): "Multi-access Edge Computing (MEC); Phase 2: Use Cases and Requirements".
2. ETSI GS MEC 010-1 (V1.1.1) (10-2017): "Mobile Edge Computing (MEC); Mobile Edge Management; Part 1: System, host and platform management".
3. ETSI GS MEC 010-2 (V2.2.1) (02-2022): "Multi-access Edge Computing (MEC); MEC Management; Part 2: Application lifecycle, rules and requirements management".
4. ETSI GS MEC 011 (V3.1.1) (09-2022): "Multi-access Edge Computing (MEC); Edge Platform Application Enablement".
5. ETSI GS MEC 012 (V2.2.1) (02-2022): "Multi-access Edge Computing (MEC); Radio Network Information API".
6. ETSI GS MEC 013 (V2.2.1) (01-2022): "Multi-access Edge Computing (MEC); Location API".
7. ETSI GS MEC 014 (V2.1.1) (03-2021): "Multi-access Edge Computing (MEC); UE Identity API".
8. ETSI GS MEC 015 (V2.1.1) (06-2020): "Multi-Access Edge Computing (MEC); Traffic Management APIs".
9. ETSI GS MEC 016 (V2.2.1) (04-2020): "Multi-access Edge Computing (MEC); Device application interface".
10. ETSI GS MEC 021 (V2.2.1) (02-2022): "Multi-access Edge Computing (MEC); Application Mobility Service API".
11. ETSI GS MEC 028 (V2.3.1) (07-2022): "Multi-access Edge Computing (MEC); WLAN Access Information API".
12. ETSI GS MEC 029 (V2.2.1) (01-2022): "Multi-access Edge Computing (MEC); Fixed Access Information API".
13. ETSI GS MEC 030 (V2.2.1) (05-2022): "Multi-access Edge Computing (MEC); V2X Information Service API".
14. ETSI GR MEC-DEC 025 (V2.1.1) (06-2019): "Multi-access Edge Computing (MEC); MEC Testing Framework".
15. ETSI GR MEC 001 (V3.1.1) (01-2022): "Multi-access Edge Computing (MEC); Terminology".
16. [The Wiki MEC web site](https://www.etsi.org/technologies/multi-access-edge-computing)
17. 